In [30]:
# Import Libraries

import math
import numpy as np 
from PIL import Image
from scipy.io import wavfile
import matplotlib.pyplot as plt
import PIL

from colormap import rgb2hex, hex2rgb
import re

In [31]:
srate, data = wavfile.read('guitar.wav')

<ipython-input-31-8b719de29572>:1: WavFileWarning: Chunk (non-data) not understood, skipping it.
  srate, data = wavfile.read('guitar.wav')


In [32]:
data.shape

(231402,)

In [49]:
def encode(file: str) -> PIL.PngImagePlugin.PngImageFile:
    
    """ Audio track encoding function.
        It takes a .wav file as input and encodes first in HEX and then in RGB.
        The output is an image with audio encoded in it
    """
    
    srate , s_arr = wavfile.read(file)
    resolution = math.ceil(np.sqrt(len(s_arr)))
    delta_res = resolution**2 - len(s_arr)
    
    new_arr = []

    buffer_symbols = ['a', 'b', 'c', 'd', 'e']
    
    
    srate_rgb = int(srate ** (1/3))
    
    for elem in s_arr:
        
        app = None
        num = 0
        salt_pos = ''.join([np.random.choice(buffer_symbols) for _ in range(6-len(str(elem)))])
        salt_neg = ''.join([np.random.choice(buffer_symbols) for _ in range(6-len(str(elem)))])
        
        if elem >= 0:
            
            app = f'#{elem}' + salt_pos
            
            print(app)
            
            new_arr.append(app)
            num += 1  
        else:
            
            app = f'#f{elem*-1}' + salt_neg
            
            print(app)
            
            new_arr.append(app)
            num += 1
            

    p_arr = np.array([list(hex2rgb(x)) for x in new_arr] + [[0,0,0] for x in range(delta_res - 1)] + [[srate_rgb, srate_rgb, srate_rgb]])
    
    p_arr = p_arr.reshape(resolution, resolution, 3)
    p_arr = p_arr.astype(np.uint8)
    
    
    img = Image.fromarray(p_arr)
    img.save(f'{file[:-4]}_encoded.png')

In [55]:
encode('guitar.wav')

<ipython-input-49-91192de04388>:8: WavFileWarning: Chunk (non-data) not understood, skipping it.
  srate , s_arr = wavfile.read(file)


#f16726
#f16396
#f16565
#f16983
#f17162
#f17071
#f16891
#f16937
#f17096
#f16909
#f16473
#f16420
#f16805
#f17207
#f17311
#f16894
#f16273
#f16101
#f16403
#f16516
#f16368
#f16345
#f16424
#f16341
#f16183
#f16174
#f16289
#f16344
#f16054
#f15420
#f14914
#f14792
#f14649
#f14192
#f13716
#f13528
#f13605
#f13742
#f13579
#f12970
#f12410
#f12309
#f12387
#f12159
#f11588
#f11039
#f10748
#f10591
#f10383
#f10082
#f9712b
#f9274d
#f8834d
#f8505e
#f8256d
#f7992e
#f7697a
#f7483c
#f7272a
#f7073c
#f6980c
#f6853b
#f6456c
#f6047d
#f6011b
#f6207e
#f6170b
#f5814e
#f5518b
#f5647c
#f5995c
#f5996d
#f5670b
#f5490d
#f5687b
#f6024a
#f6132e
#f5769e
#f5192e
#f4855e
#f4865a
#f4880b
#f4814a
#f4718d
#f4442a
#f3909a
#f3390d
#f3249e
#f3392c
#f3342e
#f2744c
#f1993a
#f1704d
#f1638e
#f1105c
#f317de
#231cce
#567bee
#899eab
#1414aa
#2101cb
#2649ac
#2858cb
#3184ee
#3887db
#4675aa
#5222ee
#5483ee
#5819ed
#6556dc
#7254db
#7498ce
#7634da
#8181dc
#8894ec
#9264aa
#9239dd
#9398ee
#10126a
#11026c
#11529e
#11584d
#11580d
#11953e
#12484c


In [56]:
def decode(path: str):
    
    """Audio decoding function from image. Uses the inverse algorithm of the encode () function
    """
    
    img = np.array(Image.open(path))
    img = img.reshape(img.shape[0]**2, 3)
    
    f_arr = []
    end_arr = []
    
    for elem in img:
        f_arr.append(rgb2hex(*elem))
        
    for h in f_arr:
        
        res = None
        
        if h[1].lower() == 'f':
            res = re.findall('\d+', h)[0]
            res = -int(res)
            end_arr.append(res)
            
        else:
            
            res = re.findall('\d+', h)[0]
            end_arr.append(int(res))
            
    
    
    end_arr = np.array(end_arr).astype(np.int16)
    
    samplerate = img[-1][-1] ** 3
    samplerate -= samplerate % -100
       
    wavfile.write(f'{path[:-4]}_decoded.wav', samplerate, end_arr)
            
            

In [58]:
decode('guitar_encoded.png')